# Wine Quality

## Import and Settings

In [59]:
import math
import optuna
import numpy as np
import pandas as pd
import scipy.stats as stats
import plotly.graph_objs as go

# Preprocessing data
from sklearn.preprocessing import RobustScaler, StandardScaler, QuantileTransformer, FunctionTransformer

# Encoder of categorical variables
from sklearn.preprocessing import OrdinalEncoder, OneHotEncoder

# Machine Learning Pipeline & process
from sklearn.pipeline import Pipeline
from sklearn.base import BaseEstimator, TransformerMixin

# ML regressors
from sklearn.linear_model import HuberRegressor,RANSACRegressor, TheilSenRegressor
from sklearn.ensemble import HistGradientBoostingRegressor, StackingRegressor, AdaBoostRegressor, RandomForestRegressor
from catboost import CatBoostRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor

# ML classifiers
from sklearn.ensemble import HistGradientBoostingClassifier, AdaBoostClassifier, RandomForestClassifier, StackingClassifier, VotingClassifier
from catboost import CatBoostClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier

# ML clusterer
from sklearn.cluster import KMeans

# Model Selection for Cross Validation
from sklearn.model_selection import StratifiedKFold, KFold, train_test_split
from sklearn.feature_selection import RFECV

# Machine Learning metrics
from sklearn.metrics import (
    mean_squared_error, 
    r2_score, 
    mean_absolute_error, 
    cohen_kappa_score, 
    make_scorer,
)

from utils import (
    seed,
    plotly_template,
    dataframe_description, 
    describe, 
    plot_correlation, 
    three_axes_scatterplot, 
    plot_histogram_matrix, 
    plot_boxplot_matrix, 
    shapiro_wilk_test, 
    barplot,
    individual_boxplot,
    violin_boxplot,
    X_y_split,
    feat_eng,
    quadratic_weighted_kappa,
    elbow_curve,
    clustered_scatterplot,
    CustomQuantileTransformer,
    CustomStandardScaler,
    KMeansTransformer,
)

## Exploratory Data Analysis

In [2]:
df = pd.read_csv('data/train.csv') # Loading data
dataframe_description(df) # Printing info on the data


DataFrame shape: (2056, 13)

2,056 samples

13 attributes

Missing Data: 

Id                      0
fixed acidity           0
volatile acidity        0
citric acid             0
residual sugar          0
chlorides               0
free sulfur dioxide     0
total sulfur dioxide    0
density                 0
pH                      0
sulphates               0
alcohol                 0
quality                 0
dtype: int64

Duplicates: 0

Data types: 

Id                        int64
fixed acidity           float64
volatile acidity        float64
citric acid             float64
residual sugar          float64
chlorides               float64
free sulfur dioxide     float64
total sulfur dioxide    float64
density                 float64
pH                      float64
sulphates               float64
alcohol                 float64
quality                   int64
dtype: object

Categorical features: 

No Categorical Features

Continuous features: 

Id
fixed acidity
volatile acidity
citric

Id  fixed acidity  volatile acidity  citric acid  residual sugar  \
0   0            8.0              0.50         0.39             2.2   
1   1            9.3              0.30         0.73             2.3   
2   2            7.1              0.51         0.03             2.1   
3   3            8.1              0.87         0.22             2.6   
4   4            8.5              0.36         0.30             2.3   

   chlorides  free sulfur dioxide  total sulfur dioxide  density    pH  \
0      0.073                 30.0                  39.0  0.99572  3.33   
1      0.092                 30.0                  67.0  0.99854  3.32   
2      0.059                  3.0                  12.0  0.99660  3.52   
3      0.084                 11.0                  65.0  0.99730  3.20   
4      0.079                 10.0                  45.0  0.99444  3.20   

   sulphates  alcohol  quality  
0       0.77     12.1        6  
1       0.67     12.8        6  
2       0.73     11.3        7  
3       0.53      9.8        5  
4       1.36      9.5        6


DataFrame Tail: 



Id  fixed acidity  volatile acidity  citric acid  residual sugar  \
2051  2051            6.6              0.31         0.13            2.00   
2052  2052            9.7              0.59         0.21            1.80   
2053  2053            7.7              0.43         0.42            1.70   
2054  2054            9.1              0.50         0.00            1.75   
2055  2055            6.2              0.31         0.18            2.30   

      chlorides  free sulfur dioxide  total sulfur dioxide  density    pH  \
2051      0.056                 29.0                  42.0  0.99388  3.52   
2052      0.079                 27.0                  65.0  0.99745  3.14   
2053      0.071                 19.0                  37.0  0.99258  3.32   
2054      0.058                  5.0                  13.0  0.99670  3.22   
2055      0.059                 12.0                  28.0  0.99520  3.56   

      sulphates  alcohol  quality  
2051       0.87     12.0        7  
2052       0.58      9.4        5  
2053       0.77     12.5        8  
2054       0.42      9.5        5  
2055       0.88     11.4        7

📝 We may drop the Id column.

📝 The dataset contains only continuous and numeric features.

📝 No NaNs nor duplicated detected.

In [3]:
df = df.drop('Id', axis = 1)  # Dropping 'Id' columns

In [4]:
describe(df)

📝 We have different scales across the attributes. We may benefit from using rescaling methods, such as StandardScaling.

In [5]:
plot_correlation(df)

📝 The highest correlated feature with the target variable quality is alcohol, with 0.48 correlation.

📝 The highest positive correlation is between citric acid and fixed acidity, at 0.7.

📝 The highest negative correlation is between ph and fixed acidity, at -0.67.

In [6]:
three_axes_scatterplot(df, 'citric acid', 'fixed acidity', 'density')

📝 In the 3D Scatterplot above, we can see the relationships between citric acid, fixed acidity, and density, which are highy-correlated features.

## Continuous Features

In [7]:
cols = df.columns.tolist()
cols.remove('quality')

In [8]:
plot_histogram_matrix(df[cols])

📝 Most distributions do not seem to follow a gaussian-like distribution (i.e., a normal distribution).

📝 residual sugar and chlorides seem to be very skewed.

In [9]:
plot_boxplot_matrix(df[cols])

📝 We have outliers present in every feature except for citric acid.

In [10]:
shapiro_wilk_test(df)

Shapiro-Wilk Test & Skewness:

- - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -  

fixed acidity

  Shapiro-Wilk Statistic: 0.94

  Shapiro-Wilk P-value: 1.0424086263516542e-28

  Skewness: 0.96

  Conclusion: fixed acidity Does Not Seem to be Normally Distributed

volatile acidity

  Shapiro-Wilk Statistic: 0.97

  Shapiro-Wilk P-value: 2.902666713071384e-20

  Skewness: 0.67

  Conclusion: volatile acidity Does Not Seem to be Normally Distributed

citric acid

  Shapiro-Wilk Statistic: 0.95

  Shapiro-Wilk P-value: 2.5441366976525463e-25

  Skewness: 0.25

  Conclusion: citric acid Does Not Seem to be Normally Distributed

residual sugar

  Shapiro-Wilk Statistic: 0.70

  Shapiro-Wilk P-value: 1.5663297997596473e-51

  Skewness: 3.75

  Conclusion: residual sugar Does Not Seem to be Normally Distributed

chlorides

  Shapiro-Wilk Statistic: 0.69

  Shapiro-Wilk P-value: 7.309053850212699e-52

  Skewness: 5.26

  Conclusion: chlor

📝 The Shapiro-Wilk test confirms the non-normality of the distributions.

In [11]:
barplot(df, 'quality')

In [12]:
individual_boxplot(df, 'quality')

📝 Most wines are classified as either 5 or 6 in quality.

📝 A low number of wines are classified as "exceptionally good" (8). An even lower number gets classified as "awful" (3).

In [13]:
for col in cols:
    violin_boxplot(df, col, 'quality', 'quality')

📝 The violin boxplot confirms the high positive correlation between alcohol and quality. The higher the alcohol, the higher the quality of the wine.

📝 Similar behavior can be seen in sulphates, as higher median values suggest higher quality.

📝 As the median value of volatile acidity gets lower, the quality gets higher. This suggests a negative correlation between this feature and the target variable.

## Feature Engineering

In [14]:
copy_df = df.copy()
copy_df.head(3)

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            8.0              0.50         0.39             2.2      0.073   
1            9.3              0.30         0.73             2.3      0.092   
2            7.1              0.51         0.03             2.1      0.059   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 30.0                  39.0  0.99572  3.33       0.77   
1                 30.0                  67.0  0.99854  3.32       0.67   
2                  3.0                  12.0  0.99660  3.52       0.73   

   alcohol  quality  
0     12.1        6  
1     12.8        6  
2     11.3        7

In [15]:
copy_df = feat_eng(copy_df)
copy_df.head(5)

fixed_acidity  volatile_acidity  citric_acid  residual_sugar  chlorides  \
0            8.0              0.50         0.39             2.2      0.073   
1            9.3              0.30         0.73             2.3      0.092   
2            7.1              0.51         0.03             2.1      0.059   
3            8.1              0.87         0.22             2.6      0.084   
4            8.5              0.36         0.30             2.3      0.079   

   free_sulfur_dioxide  total_sulfur_dioxide  density    pH  sulphates  \
0                 30.0                  39.0  0.99572  3.33       0.77   
1                 30.0                  67.0  0.99854  3.32       0.67   
2                  3.0                  12.0  0.99660  3.52       0.73   
3                 11.0                  65.0  0.99730  3.20       0.53   
4                 10.0                  45.0  0.99444  3.20       1.36   

   alcohol  quality  total_acidity  acidity_to_pH_ratio  \
0     12.1        6           8.89             2.669670   
1     12.8        6          10.33             3.111446   
2     11.3        7           7.64             2.170455   
3      9.8        5           9.19             2.871875   
4      9.5        6           9.16             2.862500   

   free_sulfur_dioxide_to_total_sulfur_dioxide_ratio  \
0                                           0.769231   
1                                           0.447761   
2                                           0.250000   
3                                           0.169231   
4                                           0.222222   

   alcohol_to_acidity_ratio  residual_sugar_to_citric_acid_ratio  \
0                  1.361080                             5.641026   
1                  1.239109                             3.150685   
2                  1.479058                            70.000000   
3                  1.066376                            11.818182   
4                  1.037118                             7.666667   

   alcohol_to_density_ratio  total_alkalinity  total_minerals  
0                 12.152011             15.43           3.043  
1                 12.818715             16.12           3.062  
2                 11.338551             14.82           2.889  
3                  9.826532             13.00           3.214  
4                  9.553115             12.70           3.739

In [16]:
X, y = X_y_split(copy_df, 'quality')


X shape: (2056, 19)


2056 Samples 


19 Attributes 



fixed_acidity  volatile_acidity  citric_acid  residual_sugar  chlorides  \
0            8.0              0.50         0.39             2.2      0.073   
1            9.3              0.30         0.73             2.3      0.092   
2            7.1              0.51         0.03             2.1      0.059   
3            8.1              0.87         0.22             2.6      0.084   
4            8.5              0.36         0.30             2.3      0.079   
5            9.9              0.51         0.44             2.2      0.111   
6            7.2              0.87         0.00             2.3      0.080   
7            7.5              0.43         0.32             1.8      0.066   
8           11.6              0.38         0.55             2.2      0.084   
9            7.8              0.78         0.09             2.2      0.049   

   free_sulfur_dioxide  total_sulfur_dioxide  density    pH  sulphates  \
0                 30.0                  39.0  0.99572  3.33       0.77   
1                 30.0                  67.0  0.99854  3.32       0.67   
2                  3.0                  12.0  0.99660  3.52       0.73   
3                 11.0                  65.0  0.99730  3.20       0.53   
4                 10.0                  45.0  0.99444  3.20       1.36   
5                 30.0                 134.0  0.99820  3.11       0.54   
6                  6.0                  18.0  0.99552  3.34       0.60   
7                 18.0                  40.0  0.99560  3.30       0.43   
8                 17.0                  40.0  1.00080  3.17       0.73   
9                 13.0                  29.0  0.99682  3.51       0.49   

   alcohol  total_acidity  acidity_to_pH_ratio  \
0     12.1           8.89             2.669670   
1     12.8          10.33             3.111446   
2     11.3           7.64             2.170455   
3      9.8           9.19             2.871875   
4      9.5           9.16             2.862500   
5      9.6          10.85             3.488746   
6     11.3           8.07             2.416168   
7      9.7           8.25             2.500000   
8      9.8          12.53             3.952681   
9      9.5           8.67             2.470085   

   free_sulfur_dioxide_to_total_sulfur_dioxide_ratio  \
0                                           0.769231   
1                                           0.447761   
2                                           0.250000   
3                                           0.169231   
4                                           0.222222   
5                                           0.223881   
6                                           0.333333   
7                                           0.450000   
8                                           0.425000   
9                                           0.448276   

   alcohol_to_acidity_ratio  residual_sugar_to_citric_acid_ratio  \
0                  1.361080                             5.641026   
1                  1.239109                             3.150685   
2                  1.479058                            70.000000   
3                  1.066376                            11.818182   
4                  1.037118                             7.666667   
5                  0.884793                             5.000000   
6                  1.400248                             0.000000   
7                  1.175758                             5.625000   
8                  0.782123                             4.000000   
9                  1.095732                            24.444444   

   alcohol_to_density_ratio  total_alkalinity  total_minerals  
0                 12.152011             15.43           3.043  
1                 12.818715             16.12           3.062  
2                 11.338551             14.82           2.889  
3                  9.826532             13.00           3.214  
4                  9.553115             12.70           3.739  
5                  9.617311 




y shape: (2056,)


2056 Samples 



0    6
1    6
2    7
3    5
4    6
5    5
6    6
7    6
8    6
9    5
Name: quality, dtype: int64

In [17]:
has_negatives = np.any(X <= 0)

if has_negatives:
    print("There are negative values in the data.")
else:
    print("There are no negative values in the data.")

There are negative values in the data.


📝 By confirming the existance of negative values in the data, I decided to use QuantileTransformer.

In [18]:
transformer = QuantileTransformer(output_distribution='normal')
X_transformed = transformer.fit_transform(X)
X_transformed = pd.DataFrame(X_transformed, columns=X.columns)
plot_histogram_matrix(X_transformed)

In [19]:
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_transformed)
X_scaled = pd.DataFrame(X_scaled, columns=X_transformed.columns)
describe(X_scaled)

## Feature Selection

In [20]:
cv = StratifiedKFold(n_splits = 5,shuffle = True, random_state = seed)
cv_splits = list(cv.split(X,y))

In [21]:
estimator = RandomForestClassifier(random_state=seed)
rfe = RFECV(estimator=estimator, cv=cv, scoring=make_scorer(quadratic_weighted_kappa))
rfe.fit(X, y)

selected_features = []

for i, feature in enumerate(X_scaled.columns):
    if rfe.support_[i]:
        selected_features.append(feature)

print(f'{len(selected_features)} features selected out of {len(X_scaled.columns)}.')
print(f'\nSelected Features: \n')
for feature in selected_features:
    print(feature)

16 features selected out of 19.

Selected Features: 

volatile_acidity
citric_acid
chlorides
total_sulfur_dioxide
density
pH
sulphates
alcohol
total_acidity
acidity_to_pH_ratio
free_sulfur_dioxide_to_total_sulfur_dioxide_ratio
alcohol_to_acidity_ratio
residual_sugar_to_citric_acid_ratio
alcohol_to_density_ratio
total_alkalinity
total_minerals


In [22]:
X_scaled = X_scaled[selected_features]
X_scaled.head(5)

volatile_acidity  citric_acid  chlorides  total_sulfur_dioxide   density  \
0         -0.076330     0.508947  -0.553589             -0.142310 -0.566442   
1         -1.361933     1.730563   0.770374              0.745626  1.004572   
2         -0.023067    -0.351927  -1.336598             -1.626645 -0.042952   
3          1.770765     0.067305   0.377988              0.657764  0.310036   
4         -0.857373     0.321729  -0.025974              0.049100 -1.420972   

         pH  sulphates   alcohol  total_acidity  acidity_to_pH_ratio  \
0  0.155189   0.953842  1.406556       0.079472            -0.009198   
1  0.099862   0.410132  2.038955       0.816195             0.701172   
2  1.314119   0.755430  0.798575      -0.917450            -1.087849   
3 -0.708869  -0.868483 -0.301802       0.263831             0.321004   
4 -0.708869   2.997112 -0.754706       0.247136             0.304314   

   free_sulfur_dioxide_to_total_sulfur_dioxide_ratio  \
0                                           2.329995   
1                                           0.492392   
2                                          -0.751248   
3                                          -1.583415   
4                                          -1.022301   

   alcohol_to_acidity_ratio  residual_sugar_to_citric_acid_ratio  \
0                  0.777777                            -0.019915   
1                  0.338287                            -0.457675   
2                  1.198958                             1.036371   
3                 -0.375436                             0.506149   
4                 -0.501615                             0.202630   

   alcohol_to_density_ratio  total_alkalinity  total_minerals  
0                  1.407556          1.421266        0.183914  
1                  1.941568          2.034824        0.216886  
2                  0.791176          0.925482       -0.095595  
3                 -0.316459         -0.439173        0.493229  
4                 -0.601954         -0.952784        1.189350

## Clustering

In [23]:
wss_values = []
for k in range(1,10):
    kmeans = KMeans(n_clusters = k, random_state = seed)
    kmeans.fit(X_scaled) 
    wss_values.append(kmeans.inertia_) 
elbow_curve(wss_values)

In [24]:
kmeans = KMeans(n_clusters = 3, random_state = seed)
kmeans.fit(X_scaled)
X_scaled['Cluster_3'] = kmeans.labels_
clustered_scatterplot(X_scaled, 'sulphates', 'alcohol_to_density_ratio', 'Cluster_3')

Cluster Count:
Cluster_3
0    753
1    745
2    558
Name: count, dtype: int64


In [25]:
kmeans = KMeans(n_clusters = 4, random_state = seed)
kmeans.fit(X_scaled)
X_scaled['Cluster_4'] = kmeans.labels_
clustered_scatterplot(X_scaled, 'sulphates', 'alcohol_to_density_ratio', 'Cluster_4')

Cluster Count:
Cluster_4
0    735
3    635
2    478
1    208
Name: count, dtype: int64


📝 It seems like $K=3$ is able to better group the data.

📝 We can clearly see that cluster 0 is more concentrated towards negative values, while cluster 1 is more concentrated towards positive values. cluster 2 gets grouped towards the middle.

## Modelling

In [26]:
df

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0               8.0              0.50         0.39            2.20      0.073   
1               9.3              0.30         0.73            2.30      0.092   
2               7.1              0.51         0.03            2.10      0.059   
3               8.1              0.87         0.22            2.60      0.084   
4               8.5              0.36         0.30            2.30      0.079   
...             ...               ...          ...             ...        ...   
2051            6.6              0.31         0.13            2.00      0.056   
2052            9.7              0.59         0.21            1.80      0.079   
2053            7.7              0.43         0.42            1.70      0.071   
2054            9.1              0.50         0.00            1.75      0.058   
2055            6.2              0.31         0.18            2.30      0.059   

      free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                    30.0                  39.0  0.99572  3.33       0.77   
1                    30.0                  67.0  0.99854  3.32       0.67   
2                     3.0                  12.0  0.99660  3.52       0.73   
3                    11.0                  65.0  0.99730  3.20       0.53   
4                    10.0                  45.0  0.99444  3.20       1.36   
...                   ...                   ...      ...   ...        ...   
2051                 29.0                  42.0  0.99388  3.52       0.87   
2052                 27.0                  65.0  0.99745  3.14       0.58   
2053                 19.0                  37.0  0.99258  3.32       0.77   
2054                  5.0                  13.0  0.99670  3.22       0.42   
2055                 12.0                  28.0  0.99520  3.56       0.88   

      alcohol  quality  
0        12.1        6  
1        12.8        6  
2        11.3        7  
3         9.8        5  
4         9.5        6  
...       ...      ...  
2051     12.0        7  
2052      9.4        5  
2053     12.5        8  
2054      9.5        5  
2055     11.4        7  

[2056 rows x 12 columns]

In [27]:
pipeline = Pipeline([
    ('Feature Engineering', FunctionTransformer(feat_eng)),
    ('Transforming Distribution', CustomQuantileTransformer()),
    ('Standard Scaler', CustomStandardScaler()),
    ('Clustering', KMeansTransformer()),
    ('Model', None)
])

In [33]:
pipeline

Pipeline(steps=[('Feature Engineering',
                 FunctionTransformer(func=<function feat_eng at 0x00000214708BF560>)),
                ('Transforming Distribution', CustomQuantileTransformer()),
                ('Standard Scaler', CustomStandardScaler()),
                ('Clustering', KMeansTransformer()),
                ('Model', HistGradientBoostingClassifier(random_state=42))])

In [29]:
X, y = X_y_split(df, 'quality')


X shape: (2056, 11)


2056 Samples 


11 Attributes 



fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            8.0              0.50         0.39             2.2      0.073   
1            9.3              0.30         0.73             2.3      0.092   
2            7.1              0.51         0.03             2.1      0.059   
3            8.1              0.87         0.22             2.6      0.084   
4            8.5              0.36         0.30             2.3      0.079   
5            9.9              0.51         0.44             2.2      0.111   
6            7.2              0.87         0.00             2.3      0.080   
7            7.5              0.43         0.32             1.8      0.066   
8           11.6              0.38         0.55             2.2      0.084   
9            7.8              0.78         0.09             2.2      0.049   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 30.0                  39.0  0.99572  3.33       0.77   
1                 30.0                  67.0  0.99854  3.32       0.67   
2                  3.0                  12.0  0.99660  3.52       0.73   
3                 11.0                  65.0  0.99730  3.20       0.53   
4                 10.0                  45.0  0.99444  3.20       1.36   
5                 30.0                 134.0  0.99820  3.11       0.54   
6                  6.0                  18.0  0.99552  3.34       0.60   
7                 18.0                  40.0  0.99560  3.30       0.43   
8                 17.0                  40.0  1.00080  3.17       0.73   
9                 13.0                  29.0  0.99682  3.51       0.49   

   alcohol  
0     12.1  
1     12.8  
2     11.3  
3      9.8  
4      9.5  
5      9.6  
6     11.3  
7      9.7  
8      9.8  
9      9.5




y shape: (2056,)


2056 Samples 



0    6
1    6
2    7
3    5
4    6
5    5
6    6
7    6
8    6
9    5
Name: quality, dtype: int64

In [30]:
cv = StratifiedKFold(n_splits = 5,shuffle = True, random_state = seed)
cv_splits = list(cv.split(X,y))

In [31]:
# List of classification algorithms
classifiers = [
    ('CatBoost', CatBoostClassifier(random_state = seed, verbose = False)),
    ('LightGBM', LGBMClassifier(random_state = seed)),
    #('XGboost', XGBClassifier(random_state = seed)),
    ('Ada Boost', AdaBoostClassifier(random_state = seed)),
    ('Histogram-based Gradient Boosting', HistGradientBoostingClassifier(random_state = seed))
]

In [32]:
print('\nCross-Validation:')
for j, (name, clf) in enumerate(classifiers):
    scores = []
    r2_scores = []
    pipeline.set_params(Model = clf)
    
    print('\n')
    print(f'\n{name} Classifier:\n')
    
    for i, (train_index, val_index) in enumerate(cv_splits):
        X_train, X_val = X.iloc[train_index], X.iloc[val_index]
        y_train, y_val = y.iloc[train_index], y.iloc[val_index]
        
        pipeline.fit(X_train, y_train)
        y_pred = pipeline.predict(X_val)
        
        kappa = cohen_kappa_score(y_val, y_pred, weights = 'quadratic')
        
        print(f'Fold {i + 1}:\n')
        print(f'  Quadratic Weighted Kappa = {kappa:.4f}')
        
        scores.append(kappa)
        
        print('===================================================')
    
    if i == len(cv_splits) - 1:
        mean_score = np.mean(scores)
        fold_std = np.std(scores)
        
        print(f'\n  Mean Quadratic Weighted Kappa = = {mean_score:.4f} \u00B1 {fold_std:.4f}')


Cross-Validation:



CatBoost Classifier:

Fold 1:

  Quadratic Weighted Kappa = 0.5066
Fold 2:

  Quadratic Weighted Kappa = 0.5053
Fold 3:

  Quadratic Weighted Kappa = 0.4644
Fold 4:

  Quadratic Weighted Kappa = 0.4735
Fold 5:

  Quadratic Weighted Kappa = 0.5012

  Mean Quadratic Weighted Kappa = = 0.4902 ± 0.0177



LightGBM Classifier:

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001284 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2921
[LightGBM] [Info] Number of data points in the train set: 1644, number of used features: 20
[LightGBM] [Info] Start training from score -5.207663
[LightGBM] [Info] Start training from score -3.620698
[LightGBM] [Info] Start training from score -0.894629
[LightGBM] [Info] Start training from score -0.971947
[LightGBM] [Info] Start training from score -1.821391
[LightGBM] [Info] Start trainin

In [45]:
def objective(trial):
    params = {
        'loss': trial.suggest_categorical('loss', ['log_loss']),
        'learning_rate': trial.suggest_float('learning_rate', 0.1, 1.0, step = 0.2),
        'max_iter': trial.suggest_int('max_iter', 100, 1000, step = 50),
        'max_leaf_nodes': trial.suggest_int('max_leaf_nodes', 30, 10000, step = 100),
        'max_depth': trial.suggest_int('max_depth', 30, 10000, step = 100),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 10, 1000, step = 15),
        'l2_regularization': trial.suggest_float('l2_regularization', 0.01, 100, step = 0.05),
        'class_weight': trial.suggest_categorical('class_weight', ['balanced', None])
    }
    
    pipeline.set_params(Model = HistGradientBoostingClassifier(**params, random_state = seed))
    scores = []
    
    for i, (train_index, val_index) in enumerate(cv_splits):
        X_train, X_val = X.iloc[train_index], X.iloc[val_index]
        y_train, y_val = y.iloc[train_index], y.iloc[val_index]
        
        pipeline.fit(X_train, y_train)
        y_pred = pipeline.predict(X_val)
        
        kappa = cohen_kappa_score(y_val, y_pred, weights = 'quadratic')
        
        print(f'Fold {i + 1}:\n')
        print(f'  Quadratic Weighted Kappa = {kappa:.4f}\n')
        
        scores.append(kappa)
    
    if i == len(cv_splits) - 1:
        mean_score = np.mean(scores)
           
        print('* * * * * * * * * * * * * * * * * * * * * * * * * * * *\n')
        print(f'  Mean Quadratic Weighted Kappa: {mean_score:.4f}\n')
        print('\n')
        
    return mean_score

In [46]:
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials = 100, show_progress_bar = True)

[I 2024-09-11 16:42:21,379] A new study created in memory with name: no-name-ae44482d-80a5-471f-9759-9851746fa5f7


  0%|          | 0/100 [00:00<?, ?it/s]

Fold 1:

  Quadratic Weighted Kappa = 0.3890

Fold 2:

  Quadratic Weighted Kappa = 0.4179

Fold 3:

  Quadratic Weighted Kappa = 0.4033

Fold 4:

  Quadratic Weighted Kappa = 0.4299

Fold 5:

  Quadratic Weighted Kappa = 0.4690

* * * * * * * * * * * * * * * * * * * * * * * * * * * *

  Mean Quadratic Weighted Kappa: 0.4218



[I 2024-09-11 16:42:36,783] Trial 0 finished with value: 0.42180687120000704 and parameters: {'loss': 'log_loss', 'learning_rate': 0.7000000000000001, 'max_iter': 950, 'max_leaf_nodes': 5130, 'max_depth': 2630, 'min_samples_leaf': 160, 'l2_regularization': 16.860000000000003, 'class_weight': 'balanced'}. Best is trial 0 with value: 0.42180687120000704.
Fold 1:

  Quadratic Weighted Kappa = 0.4448

Fold 2:

  Quadratic Weighted Kappa = 0.4665

Fold 3:

  Quadratic Weighted Kappa = 0.4483

Fold 4:

  Quadratic Weighted Kappa = 0.4804

Fold 5:

  Quadratic Weighted Kappa = 0.4793

* * * * * * * * * * * * * * * * * * * * * * * * * * * *

  Mean Quadratic Weighted Ka

In [47]:
best_params = study.best_params
best_rmse_score = study.best_value


print(f'\nHistogram-based Gradient Boosting Regressor:\n')
print(f'\n Best RMSE score = {best_rmse_score} \n')
print(f'\n Best Params = {best_params} \n')


Histogram-based Gradient Boosting Regressor:


 Best RMSE score = 0.5026611854503422 


 Best Params = {'loss': 'log_loss', 'learning_rate': 0.1, 'max_iter': 400, 'max_leaf_nodes': 3030, 'max_depth': 7130, 'min_samples_leaf': 280, 'l2_regularization': 54.06, 'class_weight': None} 



In [48]:
def objective2(trial):
    params = {
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.5, step=0.01),
        'iterations': trial.suggest_int('iterations', 100, 1000, step=50),
        'max_depth': trial.suggest_int('max_depth', 4, 10),
        'subsample': trial.suggest_float('subsample', 0.1, 1.0, step=0.1),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 0.1, 10, step=0.1),
        'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 1, 50),
        'random_strength': trial.suggest_float('random_strength', 0.1, 10, step=0.1),
        'verbose': False,
        'bootstrap_type': trial.suggest_categorical('bootstrap_type', ['Bernoulli', 'MVS']),
        'grow_policy': trial.suggest_categorical('grow_policy', ['SymmetricTree', 'Depthwise', 'Lossguide']),
        'leaf_estimation_method': trial.suggest_categorical('leaf_estimation_method', ['Newton', 'Gradient']),
        'eval_metric': 'Accuracy'
    }
    
    pipeline.set_params(Model = CatBoostClassifier(**params, random_state = seed))
    scores = []
    
    for i, (train_index, val_index) in enumerate(cv_splits):
        X_train, X_val = X.iloc[train_index], X.iloc[val_index]
        y_train, y_val = y.iloc[train_index], y.iloc[val_index]
        
        pipeline.fit(X_train, y_train)
        y_pred = pipeline.predict(X_val)
        
        kappa = cohen_kappa_score(y_val, y_pred, weights = 'quadratic')
        
        print(f'Fold {i + 1}:\n')
        print(f'  Quadratic Weighted Kappa = {kappa:.4f}\n')
        
        scores.append(kappa)
    
    if i == len(cv_splits) - 1:
        mean_score = np.mean(scores)
        
        print('* * * * * * * * * * * * * * * * * * * * * * * * * * * *\n')
        print(f'  Mean Quadratic Weighted Kappa: {mean_score:.4f}\n')
        print('\n')
        
    return mean_score        

In [49]:
study2 = optuna.create_study(direction='maximize')
study2.optimize(objective2, n_trials = 100, show_progress_bar = True)

[I 2024-09-11 17:06:14,938] A new study created in memory with name: no-name-63d85c06-f99a-4676-be2d-f8c8b23a8d15


  0%|          | 0/100 [00:00<?, ?it/s]

Fold 1:

  Quadratic Weighted Kappa = 0.4524

Fold 2:

  Quadratic Weighted Kappa = 0.5316

Fold 3:

  Quadratic Weighted Kappa = 0.4575

Fold 4:

  Quadratic Weighted Kappa = 0.4531

Fold 5:

  Quadratic Weighted Kappa = 0.4881

* * * * * * * * * * * * * * * * * * * * * * * * * * * *

  Mean Quadratic Weighted Kappa: 0.4766



[I 2024-09-11 17:06:50,161] Trial 0 finished with value: 0.476550616923949 and parameters: {'learning_rate': 0.17, 'iterations': 450, 'max_depth': 4, 'subsample': 0.6, 'l2_leaf_reg': 2.8000000000000003, 'min_data_in_leaf': 48, 'random_strength': 1.4000000000000001, 'bootstrap_type': 'Bernoulli', 'grow_policy': 'SymmetricTree', 'leaf_estimation_method': 'Gradient'}. Best is trial 0 with value: 0.476550616923949.
Fold 1:

  Quadratic Weighted Kappa = 0.4240

Fold 2:

  Quadratic Weighted Kappa = 0.4402

Fold 3:

  Quadratic Weighted Kappa = 0.4088

Fold 4:

  Quadratic Weighted Kappa = 0.4811

Fold 5:

  Quadratic Weighted Kappa = 0.4705

* * * * * * * * * * * * *

In [50]:
best_params2 = study2.best_params
best_rmse_score2 = study2.best_value


print(f'\nCatBoost Regressor:\n')
print(f'\n Best RMSE score = {best_rmse_score2} \n')
print(f'\n Best Params = {best_params2} \n')


CatBoost Regressor:


 Best RMSE score = 0.514093217059668 


 Best Params = {'learning_rate': 0.04, 'iterations': 700, 'max_depth': 4, 'subsample': 0.1, 'l2_leaf_reg': 5.8, 'min_data_in_leaf': 19, 'random_strength': 5.0, 'bootstrap_type': 'MVS', 'grow_policy': 'Depthwise', 'leaf_estimation_method': 'Gradient'} 



In [51]:
# Creating list of the tuned models
estimators = [
    ('CatBoost Regressor', CatBoostClassifier(**best_params2, random_state = seed, verbose = False)),
    ('Histogram-based Gradient Boosting', HistGradientBoostingClassifier(**best_params ,random_state = seed))
]

In [52]:
# Creating a stackingclassifier model
stacking_model = StackingClassifier(estimators = estimators, n_jobs = 5)

In [53]:
# Visualizing Pipeline
pipeline.set_params(Model = stacking_model)
pipeline

Pipeline(steps=[('Feature Engineering',
                 FunctionTransformer(func=<function feat_eng at 0x00000214708BF560>)),
                ('Transforming Distribution', CustomQuantileTransformer()),
                ('Standard Scaler', CustomStandardScaler()),
                ('Clustering', KMeansTransformer()),
                ('Model',
                 StackingClassifier(estimators=[('CatBoost Regressor',
                                                 <catboost.core.CatBoostClassifier object at 0x000002147FA86AE0>),
                                                ('Histogram-based Gradient '
                                                 'Boosting',
                                                 HistGradientBoostingClassifier(l2_regularization=54.06,
                                                                                max_depth=7130,
                                                                                max_iter=400,
                                                                                max_leaf_nodes=3030,
                                                                                min_samples_leaf=280,
                                                                                random_state=42))],
                                    n_jobs=5))])

In [54]:
print('\nStacking Classifier Cross-Validation:')
scores = []
print('\n')
print(f'\nStacking Classifier w/ CatBoost Classifier and Histogram-based Gradient Boosting Classifier :\n')
    
for i, (train_index, val_index) in enumerate(cv_splits):
    X_train, X_val = X.iloc[train_index], X.iloc[val_index]
    y_train, y_val = y.iloc[train_index], y.iloc[val_index]
        
    pipeline.fit(X_train, y_train)
    y_pred = pipeline.predict(X_val)
        
    kappa = cohen_kappa_score(y_val, y_pred, weights = 'quadratic')
        
    print(f'Fold {i + 1}:\n')
    print(f'  Quadratic Weighted Kappa = {kappa:.4f}')
        
    scores.append(kappa)
        
    print('===================================================')
    
    if i == len(cv_splits) - 1:
        mean_score = np.mean(scores)
        fold_std = np.std(scores)
        
        print(f'\n  Mean Quadratic Weighted Kappa = = {mean_score:.4f} \u00B1 {fold_std:.4f}')


Stacking Classifier Cross-Validation:



Stacking Classifier w/ CatBoost Classifier and Histogram-based Gradient Boosting Classifier :

Fold 1:

  Quadratic Weighted Kappa = 0.4744
Fold 2:

  Quadratic Weighted Kappa = 0.5417
Fold 3:

  Quadratic Weighted Kappa = 0.5081
Fold 4:

  Quadratic Weighted Kappa = 0.5282
Fold 5:

  Quadratic Weighted Kappa = 0.5401

  Mean Quadratic Weighted Kappa = = 0.5185 ± 0.0251


In [55]:
# Creating VotingClassifier model
voting_model = VotingClassifier(estimators = estimators, n_jobs = 5, voting = 'soft')

In [56]:
# Setting and visualizing pipeline
pipeline.set_params(Model = voting_model)
pipeline

Pipeline(steps=[('Feature Engineering',
                 FunctionTransformer(func=<function feat_eng at 0x00000214708BF560>)),
                ('Transforming Distribution', CustomQuantileTransformer()),
                ('Standard Scaler', CustomStandardScaler()),
                ('Clustering', KMeansTransformer()),
                ('Model',
                 VotingClassifier(estimators=[('CatBoost Regressor',
                                               <catboost.core.CatBoostClassifier object at 0x000002147FA86AE0>),
                                              ('Histogram-based Gradient '
                                               'Boosting',
                                               HistGradientBoostingClassifier(l2_regularization=54.06,
                                                                              max_depth=7130,
                                                                              max_iter=400,
                                                                              max_leaf_nodes=3030,
                                                                              min_samples_leaf=280,
                                                                              random_state=42))],
                                  n_jobs=5, voting='soft'))])

In [57]:
print('\nVoting Classifier Cross-Validation:')
scores = []
print('\n')
print(f'\nVoting Classifier w/ CatBoost Classifier and Histogram-based Gradient Boosting Classifier :\n')
    
for i, (train_index, val_index) in enumerate(cv_splits):
    X_train, X_val = X.iloc[train_index], X.iloc[val_index]
    y_train, y_val = y.iloc[train_index], y.iloc[val_index]
        
    pipeline.fit(X_train, y_train)
    y_pred = pipeline.predict(X_val)
        
    kappa = cohen_kappa_score(y_val, y_pred, weights = 'quadratic')
        
    print(f'Fold {i + 1}:\n')
    print(f'  Quadratic Weighted Kappa = {kappa:.4f}')
        
    scores.append(kappa)
        
    print('===================================================')
    
    if i == len(cv_splits) - 1:
        mean_score = np.mean(scores)
        fold_std = np.std(scores)
        
        print(f'\n  Mean Quadratic Weighted Kappa = = {mean_score:.4f} \u00B1 {fold_std:.4f}')


Voting Classifier Cross-Validation:



Voting Classifier w/ CatBoost Classifier and Histogram-based Gradient Boosting Classifier :

Fold 1:

  Quadratic Weighted Kappa = 0.4849
Fold 2:

  Quadratic Weighted Kappa = 0.5345
Fold 3:

  Quadratic Weighted Kappa = 0.5001
Fold 4:

  Quadratic Weighted Kappa = 0.5091
Fold 5:

  Quadratic Weighted Kappa = 0.5066

  Mean Quadratic Weighted Kappa = = 0.5070 ± 0.0161


In [60]:
# Setting pipeline with Tuned CatBoost Model
pipeline.set_params(Model = CatBoostClassifier(**best_params2,random_state = seed, verbose = False))
pipeline

Pipeline(steps=[('Feature Engineering',
                 FunctionTransformer(func=<function feat_eng at 0x00000214708BF560>)),
                ('Transforming Distribution', CustomQuantileTransformer()),
                ('Standard Scaler', CustomStandardScaler()),
                ('Clustering', KMeansTransformer()),
                ('Model',
                 <catboost.core.CatBoostClassifier object at 0x00000214723DE060>)])

In [73]:
print('\nTuned CatBoostClassifier Cross-Validation:')
scores = []
feature_importance = []
print('\n')

for i, (train_index, val_index) in enumerate(cv_splits):
    X_train, X_val = X.iloc[train_index], X.iloc[val_index]
    y_train, y_val = y.iloc[train_index], y.iloc[val_index]
        
    pipeline.fit(X_train, y_train)
    y_pred = pipeline.predict(X_val)
        
    kappa = cohen_kappa_score(y_val, y_pred, weights = 'quadratic')
        
    print(f'Fold {i + 1}:\n')
    print(f'  Quadratic Weighted Kappa = {kappa:.4f}')
        
    scores.append(kappa)
    feature_importance.append(pipeline[-1].feature_importances_)
        
    print('===================================================')
    
    if i == len(cv_splits) - 1:
        mean_score = np.mean(scores)
        fold_std = np.std(scores)
        
        print(f'\n  Mean Quadratic Weighted Kappa = = {mean_score:.4f} \u00B1 {fold_std:.4f}')


Tuned CatBoostClassifier Cross-Validation:


Fold 1:

  Quadratic Weighted Kappa = 0.4971
Fold 2:

  Quadratic Weighted Kappa = 0.5401
Fold 3:

  Quadratic Weighted Kappa = 0.4744
Fold 4:

  Quadratic Weighted Kappa = 0.5310
Fold 5:

  Quadratic Weighted Kappa = 0.5279

  Mean Quadratic Weighted Kappa = = 0.5141 ± 0.0246


In [62]:
no_model_pipeline = Pipeline(pipeline.steps[:-1])
feat_names = X.copy()
feat_names = no_model_pipeline.fit_transform(feat_names)
feature_names = feat_names.columns
mean_feature_importance = np.mean(feature_importance, axis=0)

sorted_indices = np.argsort(mean_feature_importance)[::1]
mean_feature_importance = mean_feature_importance[sorted_indices]
feature_names = feature_names[sorted_indices]

fig = go.Figure()
fig.add_trace(go.Bar(x=mean_feature_importance,y=feature_names,orientation='h'))

fig.update_layout(
    title="<b>Feature Importance <br> <sub> CatBoostClassifier</sub></b>",
    xaxis=dict(title="Feature Importance"),
    yaxis=dict(title="Features"),
    showlegend=False,
    height=600,
    width=1000,
    margin=dict(t=100, l=80),
    template= plotly_template,
    coloraxis = dict(colorscale = 'magma')
)
fig.show()

📝 sulphates seems to be the most relevant feature for predicting wine quality.

📝 Features deriving from alcohol, such as alcohol_to_density_ratio and total_alkalinity also appear to have high relevance in predicting wine quality.

## Testing Pipeline

In [64]:
test = pd.read_csv('data/test.csv')
test # Visualizing test data

Id  fixed acidity  volatile acidity  citric acid  residual sugar  \
0     2056            7.2             0.510         0.01             2.0   
1     2057            7.2             0.755         0.15             2.0   
2     2058            8.4             0.460         0.40             2.0   
3     2059            8.0             0.470         0.40             1.8   
4     2060            6.5             0.340         0.32             2.1   
...    ...            ...               ...          ...             ...   
1367  3423            8.8             0.745         0.18             2.7   
1368  3424           15.6             0.240         0.55             2.9   
1369  3425            7.3             0.760         0.00             2.2   
1370  3426            7.6             0.780         0.26             2.6   
1371  3427            8.8             0.780         0.22             3.0   

      chlorides  free sulfur dioxide  total sulfur dioxide  density    pH  \
0         0.077                 31.0                  54.0  0.99748  3.39   
1         0.102                 14.0                  35.0  0.99586  3.33   
2         0.065                 21.0                  50.0  0.99774  3.08   
3         0.056                 14.0                  25.0  0.99480  3.30   
4         0.044                  8.0                  94.0  0.99356  3.23   
...         ...                  ...                   ...      ...   ...   
1367      0.084                 41.0                 115.0  0.99823  3.38   
1368      0.062                 11.0                  25.0  0.99724  2.99   
1369      0.095                  6.0                  19.0  0.99880  3.67   
1370      0.118                 17.0                 104.0  0.99616  3.30   
1371      0.085                 21.0                  43.0  0.99790  3.37   

      sulphates  alcohol  
0          0.59      9.8  
1          0.68     10.0  
2          0.65      9.5  
3          0.65     11.7  
4          0.48     12.8  
...         ...      ...  
1367       0.70      9.8  
1368       0.77     10.1  
1369       0.60      9.4  
1370       0.53      9.9  
1371       0.56     10.2  

[1372 rows x 12 columns]

In [65]:
# Saving ids
test_id = test['Id']
test_id

0       2056
1       2057
2       2058
3       2059
4       2060
        ... 
1367    3423
1368    3424
1369    3425
1370    3426
1371    3427
Name: Id, Length: 1372, dtype: int64

In [66]:
test = test.drop('Id', axis = 1) # Removing 'Id' feature
test

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0               7.2             0.510         0.01             2.0      0.077   
1               7.2             0.755         0.15             2.0      0.102   
2               8.4             0.460         0.40             2.0      0.065   
3               8.0             0.470         0.40             1.8      0.056   
4               6.5             0.340         0.32             2.1      0.044   
...             ...               ...          ...             ...        ...   
1367            8.8             0.745         0.18             2.7      0.084   
1368           15.6             0.240         0.55             2.9      0.062   
1369            7.3             0.760         0.00             2.2      0.095   
1370            7.6             0.780         0.26             2.6      0.118   
1371            8.8             0.780         0.22             3.0      0.085   

      free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                    31.0                  54.0  0.99748  3.39       0.59   
1                    14.0                  35.0  0.99586  3.33       0.68   
2                    21.0                  50.0  0.99774  3.08       0.65   
3                    14.0                  25.0  0.99480  3.30       0.65   
4                     8.0                  94.0  0.99356  3.23       0.48   
...                   ...                   ...      ...   ...        ...   
1367                 41.0                 115.0  0.99823  3.38       0.70   
1368                 11.0                  25.0  0.99724  2.99       0.77   
1369                  6.0                  19.0  0.99880  3.67       0.60   
1370                 17.0                 104.0  0.99616  3.30       0.53   
1371                 21.0                  43.0  0.99790  3.37       0.56   

      alcohol  
0         9.8  
1        10.0  
2         9.5  
3        11.7  
4        12.8  
...       ...  
1367      9.8  
1368     10.1  
1369      9.4  
1370      9.9  
1371     10.2  

[1372 rows x 11 columns]

In [67]:
pipeline # Visualizing final pipeline

Pipeline(steps=[('Feature Engineering',
                 FunctionTransformer(func=<function feat_eng at 0x00000214708BF560>)),
                ('Transforming Distribution', CustomQuantileTransformer()),
                ('Standard Scaler', CustomStandardScaler()),
                ('Clustering', KMeansTransformer()),
                ('Model',
                 <catboost.core.CatBoostClassifier object at 0x00000214723DE060>)])

In [68]:
# Predicting with the pipeline
y_pred = pipeline.predict(test)
y_pred # Visualizing predictions

array([[5],
       [6],
       [5],
       ...,
       [5],
       [5],
       [6]], dtype=int64)

In [69]:
# Creating a submission dataframe
predictions = pd.DataFrame({
    'id': test_id,
    'quality': np.squeeze(y_pred)
})
predictions

id  quality
0     2056        5
1     2057        6
2     2058        5
3     2059        6
4     2060        6
...    ...      ...
1367  3423        5
1368  3424        6
1369  3425        5
1370  3426        5
1371  3427        6

[1372 rows x 2 columns]

## Deploying Pipeline

In [72]:
import joblib

joblib.dump(pipeline, 'wine_quality_prediction.joblib')

['wine_quality_prediction.joblib']